# Folium Route Maps Builder

By Kenneth Burchfiel

Licensed under the MIT License

This program uses Folium to convert airline flight data from the Bureau of Transportation Statistics and airport data from partow.net into route maps.

**Note**: The following files were not included in the GitHub repository because their size exceeds 100MB:
1. routes_planes_coordinates.csv
2. routes_planes_coordinates_for_mapping.csv
3. 21503323_T_T100_SEGMENT_ALL_CARRIER.csv
4. routes_planes_coordinates_for_mapping_v2.csv (used by this notebook to build the actual route maps)

You can instead retrieve these files from my copy of this project on Google Drive, available at https://drive.google.com/drive/folders/1jRTjoZtT6OWCXRTNstG9D4CxmjXe4W8q?usp=sharing .

In [1]:
import time
start_time = time.time() # Allows the program's runtime to be measured
import folium
import pandas as pd

First, I'll load in my airline flights table.

In [2]:
df_routes = pd.read_csv('routes_planes_coordinates_for_mapping_v2.csv')
# This .csv flie was created within flights_table_builder.ipynb.
df_routes.drop(columns='Unnamed: 0', inplace=True)
df_routes.reset_index(drop=True,inplace=True)

In [3]:
df_routes

DEPARTURES_SCHEDULED  DEPARTURES_PERFORMED    PAYLOAD   SEATS  \
0                        0.0                   1.0    21502.0    76.0   
1                        0.0                   3.0    64506.0   228.0   
2                        0.0                   1.0    21502.0    76.0   
3                        0.0                   1.0    21502.0    76.0   
4                        0.0                   1.0    21502.0    76.0   
...                      ...                   ...        ...     ...   
349168                1146.0                 573.0  1031400.0  5157.0   
349169                1166.0                 583.0  1049400.0  5247.0   
349170                1188.0                 594.0  1069200.0  5346.0   
349171                1216.0                 608.0  1094400.0  5472.0   
349172                1258.0                 629.0  1132200.0  5661.0   

        PASSENGERS  FREIGHT  MAIL  DISTANCE  RAMP_TO_RAMP  AIR_TIME  ...  \
0              3.0      0.0   0.0     901.0         170.0     140.0  ...   
1             75.0      0.0   0.0     228.0         219.0     140.0  ...   
2             64.0      0.0   0.0     851.0         144.0     114.0  ...   
3             55.0      0.0   0.0     122.0          58.0      31.0  ...   
4              0.0      0.0   0.0     476.0         157.0     138.0  ...   
...            ...      ...   ...       ...           ...       ...  ...   
349168      3693.0      0.0   0.0      91.0       26816.0   20972.0  ...   
349169      3646.0      0.0   0.0      91.0       27284.0   21338.0  ...   
349170      3573.0      0.0   0.0      91.0       27799.0   21740.0  ...   
349171      3827.0      0.0   0.0      91.0       28454.0   22253.0  ...   
349172      4056.0      0.0   0.0      91.0       29437.0   23021.0  ...   

        Plane_Group_Text  Code        Plane_Config_Text origin_iata_code  \
0          Jet, 2-Engine     1  Passenger Configuration              IAD   
1          Jet, 2-Engine     1  Passenger Configuration              IAD   
2          Jet, 2-Engine     1  Passenger Configuration              IAH   
3          Jet, 2-Engine     1  Passenger Configuration              ILM   
4          Jet, 2-Engine     1  Passenger Configuration              IND   
...                  ...   ...                      ...              ...   
349168  Piston, 2-Engine     1  Passenger Configuration              ACK   
349169  Piston, 2-Engine     1  Passenger Configuration              ACK   
349170  Piston, 2-Engine     1  Passenger Configuration              BOS   
349171  Piston, 2-Engine     1  Passenger Configuration              ACK   
349172  Piston, 2-Engine     1  Passenger Configuration              BOS   

       origin_lat origin_lon destination_iata_code  destination_lat  \
0          38.944    -77.456                   FLL           26.072   
1          38.944    -77.456                   JFK           40.640   
2          29.980    -95.340                   SAV           32.127   
3          34.271    -77.903                   RDU           35.877   
4          39.717    -86.294                   IAD           38.944   
...           ...        ...                   ...              ...   
349168     41.253    -70.060                   BOS           42.364   
349169     41.253    -70.060                   BOS           42.364   
349170     42.364    -71.005                   ACK           41.253   
349171     41.253    -70.060                   BOS           42.364   
349172     42.364    -71.005                   ACK           41.253   

        destination_lon  ORIGIN_DEST  
0               -80.153      FLL_IAD  
1               -73.779      IAD_JFK  
2               -81.202      IAH_SAV  
3               -78.787      ILM_RDU  
4               -77.456      IAD_IND  
...                 ...          ...  
349168          -71.005      ACK_BOS  
349169          -71.005      ACK_BOS  
349170          -70.060      ACK_BOS  
349171          -71.005      ACK_BOS  
349172          -70.060

In [4]:
df_routes.columns

Index(['DEPARTURES_SCHEDULED', 'DEPARTURES_PERFORMED', 'PAYLOAD', 'SEATS',
       'PASSENGERS', 'FREIGHT', 'MAIL', 'DISTANCE', 'RAMP_TO_RAMP', 'AIR_TIME',
       'UNIQUE_CARRIER', 'AIRLINE_ID', 'UNIQUE_CARRIER_NAME',
       'UNIQUE_CARRIER_ENTITY', 'REGION', 'CARRIER', 'CARRIER_NAME',
       'CARRIER_GROUP', 'CARRIER_GROUP_NEW', 'ORIGIN_AIRPORT_ID',
       'ORIGIN_AIRPORT_SEQ_ID', 'ORIGIN_CITY_MARKET_ID', 'ORIGIN',
       'ORIGIN_CITY_NAME', 'ORIGIN_STATE_ABR', 'ORIGIN_STATE_FIPS',
       'ORIGIN_STATE_NM', 'ORIGIN_COUNTRY', 'ORIGIN_COUNTRY_NAME',
       'ORIGIN_WAC', 'DEST_AIRPORT_ID', 'DEST_AIRPORT_SEQ_ID',
       'DEST_CITY_MARKET_ID', 'DEST', 'DEST_CITY_NAME', 'DEST_STATE_ABR',
       'DEST_STATE_FIPS', 'DEST_STATE_NM', 'DEST_COUNTRY', 'DEST_COUNTRY_NAME',
       'DEST_WAC', 'AIRCRAFT_GROUP', 'AIRCRAFT_TYPE', 'AIRCRAFT_CONFIG',
       'YEAR', 'QUARTER', 'MONTH', 'DISTANCE_GROUP', 'CLASS', 'DATA_SOURCE',
       'Unnamed: 50', 'Code_x', 'Plane_Type_Text', 'Code_y',
       'Plane_Grou

In [5]:
top_carriers = df_routes.pivot_table(values = 'DEPARTURES_PERFORMED', index = 'UNIQUE_CARRIER_NAME', aggfunc = 'sum')
top_carriers.sort_values('DEPARTURES_PERFORMED',ascending = False, inplace=True)
top_carriers.head(50)

DEPARTURES_PERFORMED
UNIQUE_CARRIER_NAME                                                     
Southwest Airlines Co.                                         1351448.0
American Airlines Inc.                                         1081960.0
Delta Air Lines Inc.                                           1024370.0
United Air Lines Inc.                                           760454.0
SkyWest Airlines Inc.                                           501360.0
JetBlue Airways                                                 361062.0
Republic Airline                                                301154.0
Alaska Airlines Inc.                                            262135.0
Envoy Air                                                       226416.0
Federal Express Corporation                                     211717.0
Endeavor Air Inc.                                               206710.0
Mesa Airlines Inc.                                              205631.0
Spirit Air Lines                                                187473.0
PSA Airlines Inc.                                               185699.0
ExpressJet Airlines LLC                                         175558.0
Frontier Airlines Inc.                                          119638.0
Compass Airlines                                                 96495.0
Hawaiian Airlines Inc.                                           88360.0
GoJet Airlines LLC d/b/a United Express                          75348.0
Horizon Air                                                      73058.0
Piedmont Airlines                                                65818.0
Trans States Airlines                                            55136.0
Air Wisconsin Airlines Corp                                      52081.0
Air Canada                                                       44590.0
United Parcel Service                                            42845.0
Westjet                                                          41862.0
Mokulele Flight Services, Inc.                                   41501.0
Cape Air                                                         40124.0
Sky Regional Airlines Inc.                                       37787.0
Commutair Aka Champlain Enterprises, Inc.                        37245.0
Allegiant Air                                                    36925.0
Jazz Aviation LP                                                 36510.0
Air Georgian                                                     35537.0
British Airways Plc                                              32433.0
Silver Airways                                                   30590.0
Atlas Air Inc.                                                   27035.0
Lufthansa German Airlines                                        24701.0
Aeromexico                                                       23245.0
Compania Panamena (Copa)                                         22378.0
Concesionaria Vuela Compania De Aviacion SA de ...               22208.0
Air Canada rouge LP                                              20505.0
Sun Country Airlines d/b/a MN Airlines                           20128.0
Corvus Airlines, Inc d/b/a Era Aviation d/b/a R...               19722.0
ABC Aerolineas SA de CV dba Interjet                             19226.0
Virgin America                                                   17734.0
Cathay Pacific Airways Ltd.                                      17714.0
Porter Airlines, Inc.                                            17403.0
Virgin Atlantic Airways                                          15637.0
ABX Air Inc                                                      15259.0
Compagnie Natl Air France                                        13406.0

In [6]:
top_aircraft = df_routes.pivot_table(values = 'DEPARTURES_PERFORMED', index = 'Plane_Type_Text', aggfunc = 'sum')
top_aircraft.sort_values('DEPARTURES_PERFORMED',ascending = False, inplace=True)
top_aircraft.head(50)
top_aircraft.to_csv('all_plane_types.csv')

I then went through all_plane_types.csv and copied the major passenger widebody aircraft in that document into the following list. (A widebody aircraft is one with two aisles, not just one.) This will make it much easier to show all widebody flights operated by U.S. airlines. 

(The list does not include some older widebody models like the MD-11 and A310, as I believe these are mostly used for freight traffic at this time.)

In [7]:
major_passenger_widebody_planes = ['Boeing 767-300/300ER', 'Boeing 777-200ER/200LR/233LR', 'Airbus Industrie A330-200', 'Boeing 777-300/300ER/333ER', 'B787-900 Dreamliner', 'Boeing 747-400', 'Airbus Industrie A330-300', 'B787-800 Dreamliner', 'Boeing 767-200/ER/EM', 'Boeing 767-400/ER', 'Airbus Industrie A380-800', 'Boeing B747-8', 'Airbus Industrie A350-900', 'Airbus Industrie A340-600', 'Airbus Industrie A340-300', 'Airbus Industrie A340-200', 'Airbus Industrie A340', 'Airbus 350-1000', 'Airbus Industrie A340-500', 'Boeing 787-10 Dreamliner'] 

The following function filters df_routes to cover a specified set of airlines, airports, and aircraft, then returns a copy of the filtered DataFrame that can be inserted into the generate_map function below.


The **departures_threshold** variable specifies the minimum number of departures for a given origin airport-destination airport pair that must be present in the table for a route to be included in the final table. Setting this variable well above 0 (to a number such as 50, for instance) prevents one-time flights from being included in the route map, and thus helps limit the route maps to regularly scheduled flights. You may need to experiment with different values in order to find the right threshold to use for a given map.

In [8]:
def route_query(data_source, airport_list = None,
airline_list = None, aircraft_list = None, departures_threshold = 0):
    df_for_mapping = data_source.copy()
    if airline_list != None: # The airline, aircraft, and airport queries will
        # only run if corresponding arguments for them were specified in the 
        # function call.
        df_for_mapping = df_for_mapping.query(
            "UNIQUE_CARRIER_NAME in @airline_list")
            # See https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.query.html
            # for an explanation of the use of @ here.
    if aircraft_list != None:
        df_for_mapping = df_for_mapping.query(
            "Plane_Type_Text in @aircraft_list")
    if airport_list != None:
        df_for_mapping = df_for_mapping.query(
            "ORIGIN in @airport_list or DEST in @airport_list")
    
    # The following code block creates a pivot table in order to count the 
    # number of departures for each origin-destination pair. Only departure
    # counts that exceed the value specified in departures_threshold will
    # be included in the final table.
    df_pivot = df_for_mapping.pivot_table(values = 'DEPARTURES_PERFORMED',
    index = ['ORIGIN_DEST', 'ORIGIN', 'DEST', 'ORIGIN_COUNTRY', 'DEST_COUNTRY',
    'origin_lat', 'origin_lon', 'destination_lat', 'destination_lon'],
    aggfunc = 'sum').sort_values('DEPARTURES_PERFORMED', ascending = False)
    df_pivot = df_pivot.query('DEPARTURES_PERFORMED >= @departures_threshold')
    df_pivot.reset_index(inplace=True)
    # The following line drops routes for which the origin and destination
    # airports are reversed. For instance, if one row shows flights from 
    # CLT to ATL and the other shows flights from ATL to CLT, one of those
    # two rows will be dropped. (Otherwise, duplicate lines will get drawn
    # on the map.) The code for producing the ORIGIN_DEST column can be 
    # found within flights_table_builder.ipynb.
    df_pivot = df_pivot.drop_duplicates('ORIGIN_DEST')
    df_pivot.reset_index(drop=True,inplace=True)

    return df_pivot

I'll first apply route_query to generate a table of all Delta flights for which
there were at least 50 departures.

In [9]:
dl_routes = route_query(data_source = df_routes,
airline_list = ['Delta Air Lines Inc.'], departures_threshold = 50)

In [10]:
dl_routes

ORIGIN_DEST ORIGIN DEST ORIGIN_COUNTRY DEST_COUNTRY  origin_lat  \
0       ATL_MCO    ATL  MCO             US           US      33.640   
1       ATL_LGA    LGA  ATL             US           US      40.777   
2       ATL_FLL    FLL  ATL             US           US      26.072   
3       ATL_TPA    ATL  TPA             US           US      33.640   
4       ATL_RDU    ATL  RDU             US           US      33.640   
..          ...    ...  ...            ...          ...         ...   
558     HAV_JFK    JFK  HAV             US           CU      40.640   
559     GIG_JFK    GIG  JFK             BR           US     -22.809   
560     ATL_RTB    ATL  RTB             US           HN      33.640   
561     SEA_TUS    SEA  TUS             US           US      47.449   
562     CZM_MSP    MSP  CZM             US           MX      44.880   

     origin_lon  destination_lat  destination_lon  DEPARTURES_PERFORMED  
0       -84.427           28.429          -81.316                5909.0  
1       -73.872           33.640          -84.427                5406.0  
2       -80.153           33.640          -84.427                4789.0  
3       -84.427           27.975          -82.533                4675.0  
4       -84.427           35.877          -78.787                4288.0  
..          ...              ...              ...                   ...  
558     -73.779           22.989          -82.409                  54.0  
559     -43.244           40.640          -73.779                  53.0  
560     -84.427           16.317          -86.522                  52.0  
561    -122.309           32.116         -110.941                  51.0  
562     -93.217           20.522          -86.926                  50.0  

[563 rows x 10 columns]

Next, I'll apply route_query to show all Delta A332 and A333 flights departing from ATL and MSP. I reduced the departures threshold to 10 to capture routes that are occasionally, but not always flown by A330s.

In [11]:
dl_a330_atl_msp_routes = route_query(data_source = df_routes, airline_list = \
['Delta Air Lines Inc.'], aircraft_list = ['Airbus Industrie A330-200',
'Airbus Industrie A330-300'], airport_list = ['ATL', 'MSP'],
departures_threshold = 10)
dl_a330_atl_msp_routes

ORIGIN_DEST ORIGIN DEST ORIGIN_COUNTRY DEST_COUNTRY  origin_lat  \
0      AMS_MSP    MSP  AMS             US           NL      44.880   
1      AMS_ATL    ATL  AMS             US           NL      33.640   
2      ATL_LHR    ATL  LHR             US           GB      33.640   
3      ATL_CDG    CDG  ATL             FR           US      49.013   
4      ATL_GRU    GRU  ATL             BR           US     -23.432   
5      ATL_FCO    ATL  FCO             US           IT      33.640   
6      ATL_LOS    ATL  LOS             US           NG      33.640   
7      ATL_DUB    ATL  DUB             US           IE      33.640   
8      CDG_MSP    MSP  CDG             US           FR      44.880   
9      ATL_SLC    ATL  SLC             US           US      33.640   
10     ATL_BCN    BCN  ATL             ES           US      41.297   
11     ATL_LAX    LAX  ATL             US           US      33.942   
12     ATL_HNL    HNL  ATL             US           US      21.316   
13     HNL_MSP    MSP  HNL             US           US      44.880   
14     ATL_CUN    CUN  ATL             MX           US      21.036   
15     CUN_MSP    MSP  CUN             US           MX      44.880   
16     ATL_PHX    ATL  PHX             US           US      33.640   
17     MCO_MSP    MCO  MSP             US           US      28.429   
18     ATL_MSP    ATL  MSP             US           US      33.640   
19     ATL_JFK    JFK  ATL             US           US      40.640   
20     ATL_DTW    DTW  ATL             US           US      42.212   

    origin_lon  destination_lat  destination_lon  DEPARTURES_PERFORMED  
0      -93.217           52.309            4.764                 775.0  
1      -84.427           52.309            4.764                 718.0  
2      -84.427           51.477           -0.461                 584.0  
3        2.550           33.640          -84.427                 358.0  
4      -46.469           33.640          -84.427                 347.0  
5      -84.427           41.813           12.253                 216.0  
6      -84.427            6.577            3.321                 209.0  
7      -84.427           53.421           -6.270                 192.0  
8      -93.217           49.013            2.550                 153.0  
9      -84.427           40.788         -111.978                 145.0  
10       2.078           33.640          -84.427                 133.0  
11    -118.408           33.640          -84.427                 110.0  
12    -157.927           33.640          -84.427                 105.0  
13     -93.217           21.316         -157.927                  88.0  
14     -86.877           33.640          -84.427                  86.0  
15     -93.217           21.036          -86.877                  72.0  
16     -84.427           33.434         -112.008                  67.0  
17     -81.316           44.880          -93.217                  31.0  
18     -84.427           44.880          -93.217                  18.0  
19     -73.779           33.640          -84.427                  15.0  
20     -83.353           33.640          -84.427                  10.0

Finally, I'll create a list of widebody flights operated by Delta. The departures threshold is still set at 10.

In [12]:
dl_widebody_routes = route_query(data_source = df_routes, airline_list = \
['Delta Air Lines Inc.'], aircraft_list = major_passenger_widebody_planes,
departures_threshold = 10)
dl_widebody_routes

ORIGIN_DEST ORIGIN DEST ORIGIN_COUNTRY DEST_COUNTRY  origin_lat  \
0       JFK_LAX    JFK  LAX             US           US      40.640   
1       AMS_DTW    DTW  AMS             US           NL      42.212   
2       AMS_ATL    AMS  ATL             NL           US      52.309   
3       AMS_MSP    MSP  AMS             US           NL      44.880   
4       JFK_LHR    JFK  LHR             US           GB      40.640   
..          ...    ...  ...            ...          ...         ...   
119     MSP_SEA    MSP  SEA             US           US      44.880   
120     JFK_SLC    SLC  JFK             US           US      40.788   
121     DTW_MSP    DTW  MSP             US           US      42.212   
122     BOS_JFK    BOS  JFK             US           US      42.364   
123     ATL_SAN    ATL  SAN             US           US      33.640   

     origin_lon  destination_lat  destination_lon  DEPARTURES_PERFORMED  
0       -73.779           33.942         -118.408                2172.0  
1       -83.353           52.309            4.764                1245.0  
2         4.764           33.640          -84.427                 941.0  
3       -93.217           52.309            4.764                 919.0  
4       -73.779           51.477           -0.461                 831.0  
..          ...              ...              ...                   ...  
119     -93.217           47.449         -122.309                  15.0  
120    -111.978           40.640          -73.779                  14.0  
121     -83.353           44.880          -93.217                  13.0  
122     -71.005           40.640          -73.779                  10.0  
123     -84.427           32.733         -117.189                  10.0  

[124 rows x 10 columns]

The following cell applies the Folium library to turn tables generated by route_query into interactive route maps.

'map_name' refers to the desired file name. 

'type' can be 'domestic' (in which only flights within the US are shown); 'international' (in which flights with an origin or destination airport outside the US are shown); or 'all', in which case all flights are shown.

'multiple_line_colors' color codes routes by departure count. I found it to be a bit of an eyesore, but feel free to experiment with it.

'show_markers' plots airport names on the map. If it's set to false, airport names will still appear when the user hovers over the airport marker within the HTML version of the site.

'domestic_view_override' focuses the map view on the US even when the map 
displays international routes. This is helpful for creating maps of airlines
whose international routes are limited mostly to North America.

In [13]:
def generate_map(df_for_mapping, map_name, type = 'all',
multiple_line_colors = False, show_markers = True,
domestic_view_override = False):    

    if (type == 'domestic') or (domestic_view_override == True):
        m = folium.Map(
            location=[40,-100], zoom_start = 5, tiles = "Stamen Terrain")
        # I really like the look of Stamen Terrain for route maps (and for maps
        # in general.)
        # 40, -100 appears to be close to the center of the contiguous US.
    else: # This map focuses on the world as a whole for international maps.
        m = folium.Map(
            location=[40,0], zoom_start = 2, tiles = "Stamen Terrain")
    if type == 'domestic':
        df_for_mapping = df_for_mapping.query(
            "ORIGIN_COUNTRY == 'US' & DEST_COUNTRY == 'US'")
        df_for_mapping.reset_index(drop=True,inplace=True)
    
    if type == 'international':
        df_for_mapping = df_for_mapping.query(
            "ORIGIN_COUNTRY != 'US' | DEST_COUNTRY != 'US'")
        df_for_mapping.reset_index(drop=True,inplace=True)

    # For each row in df_for_mapping, the following for loop stores that
    # row's origin and destination airports' latitude and longitude values into
    # variables, then graphs those lines on the map. It also creates a
    # 'tooltip' (e.g. a popup text message) showing the origin and destination
    # values of that route when the user hovers over the route line.

    for i in range(len(df_for_mapping)):

        origin_latitude = df_for_mapping.loc[i]['origin_lat']
        origin_longitude = df_for_mapping.loc[i]['origin_lon']
        destination_latitude = df_for_mapping.loc[i]['destination_lat']
        destination_longitude = df_for_mapping.loc[i]['destination_lon']
        departure_count = df_for_mapping.loc[i]['DEPARTURES_PERFORMED']
    
        route_line_color = '#3388ff' # Default Leaflet color; see
        # https://leafletjs.com/reference-1.6.0.html#path-color

        if multiple_line_colors == True:

            if departure_count > 5000:
                route_line_color = 'red'
            elif departure_count > 2500:
                route_line_color = 'orange'
            elif departure_count > 1000:
                route_line_color = 'yellow'
            elif departure_count > 500:
                route_line_color = 'green'
            else:
                route_line_color = 'blue'

        folium.vector_layers.PolyLine([(origin_latitude, origin_longitude),
        (destination_latitude, destination_longitude)], weight = 1,
        tooltip = df_for_mapping.loc[i]['ORIGIN_DEST'], 
        color = route_line_color).add_to(m)
        # Based on:
        # https://python-visualization.github.io/folium/modules.html#folium.vector_layers.PolyLine
    
    # The following set of code creates a list of all airports contained 
    # within the map, along with their coordinates. 
    origin_airports = df_for_mapping.copy()[['ORIGIN',
        'origin_lat', 'origin_lon']]
    origin_airports.columns=['code', 'lat', 'lon']
    destination_airports = df_for_mapping.copy()[['DEST',
        'destination_lat', 'destination_lon']]
    destination_airports.columns=['code', 'lat', 'lon']
    df_airports = pd.concat([origin_airports, destination_airports])
    df_airports.drop_duplicates('code', inplace=True)
    df_airports.reset_index(drop=True,inplace=True)


    # This for loop plots airport markers on the map, either as permanent
    # text values (if show_markers is set to true) or as tooltips that 
    # appear when the user hovers over the mouse (if show_values is set to 
    # False).
    # CircleMarker plots circles that mark the location of airports, while
    # DivIcon (if show_markers is set to True) plots airport codes on the 
    # map as text values.
    for i in range(len(df_airports)):
        if show_markers == True:
            folium.CircleMarker(location=[df_airports.loc[i]['lat'], 
            df_airports.loc[i]['lon']], radius = 2, fill = True,
            color = 'black', fill_color = 'black', fill_opacity = 1).add_to(m)
            # See https://leafletjs.com/reference-1.6.0.html#circlemarker
            # This version of the marker plotting code does not include
            # tooltips, as the presence of airport text on the map via the
            # DivIcon feature (see below) renders them redundant.
            folium.Marker([df_airports.loc[i]['lat'], 
            df_airports.loc[i]['lon']], 
            icon = folium.features.DivIcon(icon_anchor = (10, 20),
            html="<div><b>"+df_airports.loc[i]['code']+"</b></div>")).add_to(m)
        # The responses by Bob Haffner and lhoupert in this StackOverflow 
        # post were very helpful in getting DivIcon to work:
        # https://stackoverflow.com/questions/46400769/numbers-in-map-marker-in-folium
        # These Folium references helped also:
        # https://python-visualization.github.io/folium/modules.html#folium.map.Marker
        # https://python-visualization.github.io/folium/modules.html#folium.features.DivIcon

        else:
            folium.CircleMarker(location=[df_airports.loc[i]['lat'], 
            df_airports.loc[i]['lon']], tooltip = df_airports.loc[i]['code'],
            radius = 2, fill = True, color = 'black', fill_color = 'black',
            fill_opacity = 1).add_to(m)     
    # Before the function exits, the map gets saved to the folium_maps folder
    # using the name specified via map_name.
    m.save('folium_maps\\'+map_name+'.html')

    return m

Finally, it's time to generate some route maps! First, I'll plot a domestic route map for Delta:

In [14]:
route_map = generate_map(dl_routes, 'dl_domestic_routes_2018', type = 'domestic')
route_map

This map demonstrates that Seattle (SEA), Minneapolis (MSP), Detroit (DTW), Salt Lake City (SLC), and Atlanta (ATL) are among Delta's largest hubs.
This map does not, however, include all flights you would see on a regular route map. This is most likely because many Delta flights (along with American and United flights) are operated via regional carriers like Skywest and Envoy. I believe that these regional carriers serve multiple airlines, so combining regional and mainline carriers into a single route map could lead to inaccurate results.

Next, I'll plot an international route map:

In [15]:
route_map = generate_map(dl_routes, 'dl_international_routes_2018', 
type = 'international')
route_map

This map shows that JFK and ATL are Delta's major international hubs. The map's formatting could be improved; for instance, it would look nicer if trans-pacific routes were shown west of the US rather than east, both to make the map more readable and to better display the directions that the flights actually take. In addition, the lines could be adjusted to better match the earth's curvature. However, the map still serves as an overview of Delta's international routes.

Next, I'll create the route map showing only Delta A332 and A333 routes from ATL and MSP:

In [16]:
dl_a330_route_map = generate_map(
    dl_a330_atl_msp_routes, 'dl_a330_atl_msp_routes_2018')
dl_a330_route_map

My final Delta map will show the widebody routes contained in dl_widebody_routes.

In [17]:
dl_widebody_route_map = generate_map(
    dl_widebody_routes, 'dl_widebody_routes_2018')
dl_widebody_route_map

Next, I'll plot route maps for other carriers. The output of route_query() can be fed directly into the data_source argument of generate_map(), reducing the amount of code needed to create these maps.

In [18]:
wn_route_map = generate_map(df_for_mapping = route_query(
    data_source = df_routes,
airline_list = ['Southwest Airlines Co.'], departures_threshold = 50),
map_name = 'wn_all_routes_2018',
domestic_view_override = True)
# WN is the IATA airline code for Southwest. See:
# https://en.wikipedia.org/wiki/List_of_airline_codes
wn_route_map

This map shows that Southwest uses more of a point-to-point route system than a hub-and-spoke model, as there are fewer major hubs on this map than on Delta's. Southwest also focuses on flights within North America.

In [19]:
aa_domestic_route_map = generate_map(df_for_mapping = route_query(
data_source = df_routes,
airline_list = ['American Airlines Inc.'],
departures_threshold = 50), type = 'domestic',
map_name = 'aa_domestic_routes_2018')
aa_domestic_route_map

American Airlines has considerable hubs in Dallas, Miami, and Charlotte among other cities.

In [20]:
aa_international_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['American Airlines Inc.'], departures_threshold = 50),
    type = 'international', map_name = 'aa_international_routes_2018')
aa_international_route_map

AA has impressive coverage of South America via its MIA hub.

In [21]:
ua_domestic_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['United Air Lines Inc.'], departures_threshold = 50),
    type = 'domestic', map_name = 'ua_domestic_routes_2018')
ua_domestic_route_map

In [22]:
ua_international_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['United Air Lines Inc.'], departures_threshold = 50),
    type = 'international', map_name = 'ua_international_routes_2018')
ua_international_route_map

I find United's Guam (GUM) hub particularly interesting. I believe United inherited this hub from Continental Airlines.

In [31]:
oo_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['SkyWest Airlines Inc.'], departures_threshold = 50),
    type = 'all', map_name = 'oo_all_routes_2018',
    domestic_view_override = True)
oo_route_map

This route map shows flights operated by OO (the IATA code for SkyWest AIrlines). SkyWest operates regional flights for Alaska, Delta, United, and American Airlines. Thus, the routes shown on this map would normally be included on multiple airlines' maps. For instance, most of the SLC, MSP, and DTW flights are probably branded as Delta routes; most of the DEN and IAH flights are likely United routes; and most of the DFW flights are likely American routes. 

In [24]:
b6_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['JetBlue Airways'], departures_threshold = 50),
    type = 'all', map_name = 'b6_all_routes_2018',
    domestic_view_override = True)
b6_route_map

Here is JetBlue's route map (B6 is the IATA code for JetBlue). JetBLue's FLL and JFK hubs are the main focus of this map. 

In [25]:
as_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['Alaska Airlines Inc.'], departures_threshold = 50),
    type = 'all', map_name = 'as_all_routes_2018',
    domestic_view_override = True)
as_route_map

Alaska has considerable strength across the West Coast and in both Alaska (unsurprisingly) and Hawaii.

In [26]:
fx_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['Federal Express Corporation'],
        departures_threshold = 0),
    type = 'all', map_name = 'fx_all_routes_2018')
fx_route_map

Here is the route map for FedEx (whose IATA code is FX). I set the departures threshold to 0 to show all the FedEx routes in the data source, even ones that FedEx only flew once. Note Memphis's (MEM's) strength as both a domestic and international hub, along with ANC's use as a stopover for transpacific routes.

In [27]:
nk_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['Spirit Air Lines'],
        departures_threshold = 50),
    type = 'all', map_name = 'nk_all_routes_2018',
    domestic_view_override = True)
nk_route_map

Spirit (IATA code = NK) has a strong presence in Florida, along with other vacation destinations like LAX and LAS.

In [28]:
f9_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['Frontier Airlines Inc.'],
        departures_threshold = 50),
    type = 'all', map_name = 'f9_all_routes_2018',
    domestic_view_override = True)
f9_route_map

Frontier (IATA code = F9), another ulta-low-cost carrier, has hubs in Denver and Orlando, along with a strong presence in Austin and San Antonio.

In [29]:
g4_route_map = generate_map(
    df_for_mapping = route_query(
        data_source = df_routes,
        airline_list = ['Allegiant Air'],
        departures_threshold = 50),
    type = 'all', map_name = 'g4_all_routes_2018',
    domestic_view_override = True)
g4_route_map

As this map demonstrates, Allegiant Airlines (IATA code = G4) focuses on flying passengers to vacation hubs like Las Vegas and Florida.

I hope you enjoy using this program to create your own route maps. It will be interesting to see how the maps change over time as the airline industry continues to evolve.

In [30]:
end_time = time.time()
run_time = end_time - start_time
run_minutes = run_time // 60
run_seconds = run_time % 60
print("Completed run at",time.ctime(end_time),"(local time)")
print("Total run time:",'{:.2f}'.format(run_time),
"second(s) ("+str(run_minutes),"minute(s) and",'{:.2f}'.format(run_seconds),
"second(s))") 
# Only meaningful when the program is run nonstop from start to finish

Completed run at Fri Dec 17 17:11:20 2021 (local time)
Total run time: 17.69 second(s) (0.0 minute(s) and 17.69 second(s))
